
# 缓存最近邻

本示例演示了如何在使用KNeighborsClassifier之前预先计算k个最近邻。KNeighborsClassifier可以内部计算最近邻，但预先计算它们可以有几个好处，例如更精细的参数控制、缓存以供多次使用或自定义实现。

在这里，我们使用管道的缓存属性在多次拟合KNeighborsClassifier之间缓存最近邻图。第一次调用较慢，因为它计算了邻居图，而后续调用较快，因为它们不需要重新计算图。这里的时间较短，因为数据集较小，但当数据集变大或需要搜索的参数网格较大时，收益可能会更显著。


In [ ]:
# 作者：scikit-learn 开发者
# SPDX-License-Identifier: BSD-3-Clause
from tempfile import TemporaryDirectory

import matplotlib.pyplot as plt

from sklearn.datasets import load_digits
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier, KNeighborsTransformer
from sklearn.pipeline import Pipeline

X, y = load_digits(return_X_y=True)
n_neighbors_list = [1, 2, 3, 4, 5, 6, 7, 8, 9]

# 变换器使用网格搜索中所需的最大邻居数计算最近邻图。分类器模型根据其自身的n_neighbors参数过滤最近邻图。
graph_model = KNeighborsTransformer(n_neighbors=max(n_neighbors_list), mode="distance")
classifier_model = KNeighborsClassifier(metric="precomputed")

# 请注意，我们为 `memory` 提供了一个目录，用于缓存图计算，这将在调整分类器的超参数时多次使用。
with TemporaryDirectory(prefix="sklearn_graph_cache_") as tmpdir:
    full_model = Pipeline(
        steps=[("graph", graph_model), ("classifier", classifier_model)], memory=tmpdir
    )

    param_grid = {"classifier__n_neighbors": n_neighbors_list}
    grid_model = GridSearchCV(full_model, param_grid)
    grid_model.fit(X, y)

# 绘制网格搜索的结果。
fig, axes = plt.subplots(1, 2, figsize=(8, 4))
axes[0].errorbar(
    x=n_neighbors_list,
    y=grid_model.cv_results_["mean_test_score"],
    yerr=grid_model.cv_results_["std_test_score"],
)
axes[0].set(xlabel="n_neighbors", title="Classification accuracy")
axes[1].errorbar(
    x=n_neighbors_list,
    y=grid_model.cv_results_["mean_fit_time"],
    yerr=grid_model.cv_results_["std_fit_time"],
    color="r",
)
axes[1].set(xlabel="n_neighbors", title="Fit time (with caching)")
fig.tight_layout()
plt.show()